In [1]:
## import libraries we need 
import drifters_util as util
import numpy as np
import matplotlib.pyplot as plt
from netCDF4 import Dataset

### Plotly tools 
import plotly.graph_objs as go
import plotly.tools as tls
import plotly.express as px

import plotly.io as pio
pio.renderers.default = "notebook+pdf" 

### Diagnostics
We see a huge change in drifter location (order multiple kilometres). <br>
Need to understand if this is due to MPI parallelisation or some other issue


In [2]:
ser_directory = './Serial//'
par_directory =  './Parallel//'


times, drift_x, drift_y, drift_z = util.read_drifter(ser_directory + 'DRIFTER.OUT' )
times_par, drift_x_par, drift_y_par, drift_z_par = util.read_drifter(par_directory + 'DRIFTER.OUT' )
drift_x[drift_x==0] = np.nan
drift_x_par[drift_x_par==0] = np.nan

fig = go.Figure()
fig.add_trace(go.Scatter(x = times, y = drift_x[:,0], 
                     mode = 'markers', name = 'Serial'))
fig.add_trace(go.Scatter(x = times_par, y = drift_x_par, 
                     mode = 'markers', name = 'parallel'))
fig.update_xaxes(title_text='Time (days)')
fig.update_yaxes(title_text='X-location (km)')
fig.show()

As illustrated above, drifter moves about 6km in about 35 minutes <br>
average of about 2.8 m/s. <br>
Looking at the rate of change, we see most of the period it is reasonable <br>
varying between +- 0.5m/s
Towards the end it then increases rapidly with drifter moving at speed 3-3.5 ms (negative or West)


In [3]:
tseconds = (times - times[0]) * 86400
rate_of_change = np.diff(drift_x[:,0])/np.diff(tseconds)
rate_of_change = rate_of_change[~np.isnan(rate_of_change)]
fig = go.Figure()
fig.add_trace(go.Scatter( y = rate_of_change, 
                     mode = 'markers', name = 'Serial'))
fig.update_yaxes(title_text='rate of change (m/s)')

fig.show()

### Spatial map of trajectories

First need to read the map from a sample netcdf file


In [4]:
## use the netcdf files to generate boundary of domain
dataset_nc = Dataset('./efdcout_20150818000000.nc')
x,y,time_nc, depth = util.getcoordinates(dataset_nc, zeta = 'Elevation')
water = depth[0,:,:]

#### Now let's read the subdomain boundaries from LORP.INP

In [5]:
fname = par_directory + 'LORP.INP'
f = open(fname, "r")
lorp = f.readlines()
NH = int(lorp[3].strip(' ').split(' ')[0])
NV = int(lorp[3].strip(' ').split(' ')[1])
xsplits = []
ysplits = []
for i in range(5, 5 + NH):
    xsplits.append(int(lorp[i].strip('\n')))
for i in range(5 + NH + 1, 5 + NH + 1 + NV):
    ysplits.append(int(lorp[i].strip('\n')))

### No plot map of drifter trajectories

In [6]:

fig = go.Figure(data = 
                go.Contour(showscale=False,                        
        z=water,
        x=x, # horizontal axis
        y=y  # vertical axis
                    #3 
))
time_sel = 4
fig.add_trace(go.Scatter(x = drift_x[:,0]*1000, y = drift_y[:,0]*1000, 
                    mode = 'markers', name = 'serial'))
fig.add_trace(go.Scatter(x = drift_x_par[:,0]*1000, y = drift_y_par[:,0]*1000, 
                    mode = 'markers', name = 'parallel'))
xstep = 0 
for ndim in range(0, len(xsplits)-1):
    xstep = xstep + xsplits[ndim] - 4 # note that we add two ghost cells each side so need to remove that
    fig.add_vline(x = x[xstep])

fig.show()
